In [5]:
# -*- coding: utf-8 -*-
import json

import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from dash import Dash, dcc, html

df = pd.read_csv('DXYArea.csv').drop_duplicates(subset=['provinceName']).loc[:,
     ['provinceName', 'province_confirmedCount']].reset_index(drop=True)
names = ['陕西省', '山西省', '河南省', '湖北省']
df.loc[~df['provinceName'].isin(names), 'province_confirmedCount'] = 0
df = df.query('provinceName in @names')
df.columns = ['省份', '确诊人数']
df.loc[1,'确诊人数']=300
print(df)

with open('china.json', encoding='utf-8') as response:
    geojson = json.load(response)


def getFigure(range1=None):
    if range1 is None:
        zmin = 0
        zmax = 1272
        colors = [
            "rgb(247,251,255)",
            "rgb(222,235,247)",
            "rgb(198,219,239)",
            "rgb(158,202,225)",
        ]
    else:
        zmin = 0
        zmax = 1272*2
        colors = [
            "rgb(247,251,255)",
            "rgb(222,235,247)",
            "rgb(198,219,239)",
            "rgb(158,202,225)",
            "rgb(107,174,214)",
            "rgb(66,146,198)",
            "rgb(33,113,181)",
            "rgb(8,81,156)",
            "rgb(8,48,107)",
        ]
    print(zmin)
    print(zmax)
    fig = go.Figure(go.Choropleth(
        locations=df['省份'],
        z=df['确诊人数'],
        zmin=zmin,
        zmax=zmax,
        geojson=geojson,
        featureidkey='properties.name',
        colorscale=colors,
        locationmode='geojson-id',


    ))

    fig.update_geos(fitbounds="locations", visible=True, )
    fig.update_traces(colorbar_orientation='h', selector=dict(type='choropleth'))

    fig.update_layout(
                      geo=dict(
                          showframe=False,
                          showcoastlines=False,
                          showcountries=False,
                          showland=False,
                          showlakes=False,
                          projection_type='equirectangular',
                          bgcolor='#ffffff',
                          center={'lat': 37, 'lon': 112},
                      ),
                      )
    fig.update_traces(marker_line_color='black', selector=dict(type='choropleth'))
    return fig


app = Dash(__name__)

app.layout = html.Div([
    html.Title('疫情数据可视化'),
    html.Div([
        dcc.Graph(id='graph1', figure=getFigure()),
        # dcc.Graph(id='graph2', figure=getFigure([0, 400])),
    ],
        style={'text-align': 'center', 'margin': '0 auto'}),
])

if __name__ == '__main__':
    # app.run_server(debug=True)
    figure=getFigure([0, 400])
    figure.show()
    figure=getFigure()
    figure.show()


     省份  确诊人数
0   陕西省   245
1   湖北省   300
14  河南省  1272
27  山西省   133
0
1272
0
2544


0
1272
